In [ ]:
import os


os.chdir("../")


os.getcwd()


'd:\\DA_workspace\\alzheimers_prediction\\src'

In [ ]:
import pandas as pd
import numpy as np
from classifier.Mylib import myfuncs
from sklearn.compose import ColumnTransformer
from sklearn.impute import SimpleImputer
from sklearn.base import BaseEstimator, TransformerMixin
from sklearn.model_selection import train_test_split
import plotly.express as px
from plotly.subplots import make_subplots
from sklearn.feature_selection import (
    SelectKBest,
    mutual_info_regression,
    mutual_info_classif,
)


In [ ]:
train_data = myfuncs.load_python_object("../artifacts/data_correction/train_data.pkl")
val_data = myfuncs.load_python_object("../artifacts/data_correction/val_data.pkl")


df = pd.concat([train_data, val_data], axis=0).reset_index(drop=True)

df.head()


Age  Education_Level   BMI  Cognitive_Test_Score  do_get_Diabetes  \
0  66.0              3.0  34.9                  81.0              1.0   
1  61.0             13.0  19.8                  70.0              0.0   
2  74.0             10.0  28.8                  98.0              0.0   
3  66.0              5.0  20.5                  53.0              0.0   
4  73.0              0.0  31.4                  32.0              0.0   

   do_get_Hypertension  do_Family_History  do_get_Genetic_Risk_Factor  Gender  \
0                  1.0                0.0                         0.0    Male   
1                  0.0                0.0                         0.0    Male   
2                  1.0                0.0                         0.0    Male   
3                  0.0                0.0                         0.0  Female   
4                  1.0                0.0                         0.0  Female   

        Country  ... Alcohol_Consumption_Level Cholesterol_Level  \
0     Australia  ...                 Regularly              High   
1        Canada  ...                 Regularly            Normal   
2         Spain  ...                     Never            Normal   
3         China  ...              Occasionally              High   
4  South Africa  ...              Occasionally            Normal   

  Depression_Level Sleep_Quality_Level Diet_level  \
0              Low             Average    Average   
1           Medium                Good  Unhealthy   
2             High                Good    Average   
3           Medium                Poor  Unhealthy   
4              Low                Poor    Average   

  Air_Pollution_Exposure_level Social_Engagement_Level Income_Level  \
0                          Low                  Medium       Medium   
1                         High                     Low       Medium   
2                         High                     Low          Low   
3                       Medium                     Low         High   
4                          Low                  Medium         High   

  Stress_Levels do_get_Alzheimer  
0           Low               No  
1           Low               No  
2           Low               No  
3          High               No  
4          High              Yes  

[5 rows x 25 columns]

In [ ]:
numeric_cols = [
    "Age",
    "Education_Level",
    "BMI",
    "Cognitive_Test_Score",
]


binary_cols = [
    "do_get_Diabetes",
    "do_get_Hypertension",
    "do_Family_History",
    "do_get_Genetic_Risk_Factor",
]


nominal_cols = [
    "Gender",
    "Country",
    "Employment_Status",
    "Marital_Status",
    "living_place_urban_or_rural",
]

ordinal_cols = [
    "Physical_Activity_Level",
    "Smoking_Status_level",
    "Alcohol_Consumption_Level",
    "Cholesterol_Level",
    "Depression_Level",
    "Sleep_Quality_Level",
    "Diet_level",
    "Air_Pollution_Exposure_level",
    "Social_Engagement_Level",
    "Income_Level",
    "Stress_Levels",
]


target_col = "do_get_Alzheimer"


Cac cot numeric hien thi histogram, box plot và violinplot


In [ ]:
subplot_titles = sum(([item, "", ""] for item in numeric_cols), [])


fig = make_subplots(rows=len(numeric_cols), cols=3, subplot_titles=subplot_titles)

for row, col in enumerate(numeric_cols, 1):
    data = df[col]

    # Vẽ Histogram
    fig_hist = px.histogram(
        x=data,  # Dữ liệu cho trục X
        nbins=30,  # Số lượng cột (bins)
    )

    # Thêm đường viền cho các cột histogram
    fig_hist.update_traces(marker=dict(line=dict(width=1, color="black")))

    # Vẽ box plot
    fig_box = px.box(
        y=data,  # Dữ liệu trục Y
    )

    # Vẽ violin plot
    fig_violin = px.violin(
        y=data,  # Dữ liệu trên trục Y
        box=True,  # Hiển thị Box Plot bên trong
    )

    fig.add_trace(fig_hist.data[0], row=row, col=1)
    fig.add_trace(fig_box.data[0], row=row, col=2)
    fig.add_trace(fig_violin.data[0], row=row, col=3)

fig.update_layout(
    width=400 * 3,  # Độ rộng biểu đồ (px)
    height=len(numeric_cols) * 500,  # Độ cao biểu đồ (px)
)

fig.show()


đối với các cột cat thì hiển thị tỉ lệ chiếm trong các cột đó là được rồi


In [ ]:
df.columns


Index(['Age', 'Education_Level', 'BMI', 'Cognitive_Test_Score',
       'do_get_Diabetes', 'do_get_Hypertension', 'do_Family_History',
       'do_get_Genetic_Risk_Factor', 'Gender', 'Country', 'Employment_Status',
       'Marital_Status', 'living_place_urban_or_rural',
       'Physical_Activity_Level', 'Smoking_Status_level',
       'Alcohol_Consumption_Level', 'Cholesterol_Level', 'Depression_Level',
       'Sleep_Quality_Level', 'Diet_level', 'Air_Pollution_Exposure_level',
       'Social_Engagement_Level', 'Income_Level', 'Stress_Levels',
       'do_get_Alzheimer'],
      dtype='object')

In [ ]:
cat_cols = binary_cols + nominal_cols + ordinal_cols + [target_col]


fig = make_subplots(rows=len(cat_cols), cols=1, subplot_titles=cat_cols)

for row, col in enumerate(cat_cols, 1):
    data = df[col]

    percent = data.value_counts() / len(data) * 100

    # Vẽ Barh chart the hien ti le cua tung label
    fig_bar = px.bar(
        x=percent.values,  # Giá trị trục hoành
        y=percent.index,  # Danh mục trục tung
        orientation="h",  # Cột ngang
    )

    fig.add_trace(fig_bar.data[0], row=row, col=1)

fig.update_layout(
    width=800,  # Độ rộng biểu đồ (px)
    height=len(cat_cols) * 500,  # Độ cao biểu đồ (px)
)

fig.show()


Nhan xet ve phan bo cac gia tri

Cac cot numeric

- Cac cot co phan bo histogram kha dong deu

Cac cot cat

- cot do_get_Diabetes phan phoi ko deu, gia tri 0 vuot troi hon
- cot do_get_Hypertension phan phoi ko deu, gia tri 0 vuot troi hon
- cot do_Family_History phan phoi ko deu, gia tri 0 vuot troi hon
- cot do_get_Genetic_Risk_Factor phan phoi ko deu, gia tri 0 vuot troi hon
- cot Gender phan phoi deu
- cot Country phan phoi deu
- cot Employment_Status phan phoi deu
- cot Marital_Status phan phoi deu
- cot living_place_urban_or_rural phan phoi deu
- cot Physical_Activity_Level phan phoi deu
- cot Smoking_Status_level phan phoi deu
- cot Alcohol_Consumption_Level phan phoi deu
- cot Cholesterol_Level phan phoi ko deu, gia tri Normal vuot troi hon
- cot Depression_Level phan phoi deu
- cot Sleep_Quality_Level phan phoi deu
- cot Diet_level phan phoi deu
- cot Air_Pollution_Exposure_level phan phoi deu
- cot Social_Engagement_Level phan phoi deu
- cot Income_Level phan phoi deu
- cot Stress_Levels phan phoi deu
- cot do_get_Alzheimer phan phoi cung tam deu, gia tri No nhinh hon Yes
-
